In [1]:
import pandas as pd
import numpy as np
import math
#build model
from keras.preprocessing.image import ImageDataGenerator
from keras import Model, Sequential
from keras.applications import VGG16, VGG19
from keras.applications.inception_v3 import InceptionV3
from keras.layers import Flatten, Dense
from keras.preprocessing import image
from sklearn.model_selection import train_test_split
from keras.models import load_model
from keras.callbacks import ModelCheckpoint, LearningRateScheduler, ReduceLROnPlateau, EarlyStopping, TensorBoard, CSVLogger
import os
import argparse
import pickle
import tensorflow as tf
import keras.backend.tensorflow_backend as KTF

def parse_arg():
    parser = argparse.ArgumentParser(description='training of the baseline...')
    parser.add_argument('--gpus', type=str, default='',
                        help='gpu device')
    parser.add_argument('--name', type=str, default='',
                       help='the model name has been learned')
    args = parser.parse_args()
    os.environ['CUDA_VISIBLE_DEVICES'] = args.gpus
    return args


os.environ['CUDA_VISIBLE_DEVICES'] = "0"

"""
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True   #不全部占满显存, 按需分配
sess = tf.Session(config=config)

KTF.set_session(sess)
"""

/home/anhaoran/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


'\nconfig = tf.ConfigProto()  \nconfig.gpu_options.allow_growth=True   #不全部占满显存, 按需分配\nsess = tf.Session(config=config)\n\nKTF.set_session(sess)\n'

In [2]:
data_train = open(r'/home/anhaoran/data/zero-shot-tianchi/dataset_A/train/train.txt')
data_train = data_train.readlines()
data_dict = {}
length = len(data_train)
for i in range(length):
    m,n = data_train[i].split()
    data_dict.update({m : n})
print(len(data_dict))

data_test = open("/home/anhaoran/data/zero-shot-tianchi/dataset_A/test/image.txt")
data_test = data_test.readlines()#[:2]
length = len(data_test)
for i in range(length):
    data_dict.update({data_test[i][:-1] : "test"})
print(len(data_dict))

38221
52854


In [3]:
print(data_dict)

{'a6394b0f513290f4651cc46792e5ac86.jpeg': 'ZJL1', '2fb89ef2ace869d3eb3bdd3afe184e1c.jpeg': 'ZJL1', 'eda9f3bef2bd8da038f6acbc8355fc25.jpeg': 'ZJL1', '7d93ef45972154aae150b4f9980a79c0.jpeg': 'ZJL1', 'fb901b4f9a8e396c1d0155bccc5e5671.jpeg': 'ZJL1', '627420a22ddbd999d2ddacda932a76dc.jpeg': 'ZJL1', '730a245a524147361a459c2105d4f037.jpeg': 'ZJL1', '576edc7ddabe71fc5153048255c4104b.jpeg': 'ZJL1', 'caeb5dadde274af7118f91b591da7221.jpeg': 'ZJL1', '29949c5f44d44d12e065d378dade08be.jpeg': 'ZJL1', '1f32f8dcb25ab24e9cf9cb9f1e89b1ad.jpeg': 'ZJL1', '8a2b9140fefcaf524ff25d954d75e1a7.jpeg': 'ZJL1', '422e6a71c792e840799e7276739ea915.jpeg': 'ZJL1', '57f9fce44bd11924a11b310f767bc031.jpeg': 'ZJL1', 'd973ab6bb6f2f2f2c6ed7b54b0121df6.jpeg': 'ZJL1', '6557c8c2e9ad58e941a7ccc12de16baa.jpeg': 'ZJL1', 'f904e10682d3e2db166a476e7a0a573f.jpeg': 'ZJL1', 'aa75a7ea802f5bcb1c17c2846c5f5b59.jpeg': 'ZJL1', '85d60e82d005a9dc9bcbda4bcded220d.jpeg': 'ZJL1', '491f90eb9e2f97fd4a7a30dd80bda5dd.jpeg': 'ZJL1', '226f669584511276b1

# From here to run again

In [4]:
image_size = 224

images_all = list()
labels_all = list()
path_test = r'/home/anhaoran/data/zero-shot-tianchi/dataset_A/test/test/'
path_train = r'/home/anhaoran/data/zero-shot-tianchi/dataset_A/train/train/'
length = len(data_dict)
data_x = np.zeros((length, image_size, image_size, 3))
idx = 0
for img_name, img_label in data_dict.items():
    if img_label != "test":
        img = image.load_img(path_train + img_name, target_size=(image_size, image_size, 3))
    else:
        img = image.load_img(path_test + img_name, target_size=(image_size, image_size, 3))
    data_x[idx] = image.img_to_array(img)
    images_all.append(img_name)
    labels_all.append(img_label)
    idx += 1

print(data_x.shape)

(52854, 224, 224, 3)


In [5]:
print(len(images_all))
print(images_all)
print(len(labels_all))
print(labels_all)

52854
['a6394b0f513290f4651cc46792e5ac86.jpeg', '2fb89ef2ace869d3eb3bdd3afe184e1c.jpeg', 'eda9f3bef2bd8da038f6acbc8355fc25.jpeg', '7d93ef45972154aae150b4f9980a79c0.jpeg', 'fb901b4f9a8e396c1d0155bccc5e5671.jpeg', '627420a22ddbd999d2ddacda932a76dc.jpeg', '730a245a524147361a459c2105d4f037.jpeg', '576edc7ddabe71fc5153048255c4104b.jpeg', 'caeb5dadde274af7118f91b591da7221.jpeg', '29949c5f44d44d12e065d378dade08be.jpeg', '1f32f8dcb25ab24e9cf9cb9f1e89b1ad.jpeg', '8a2b9140fefcaf524ff25d954d75e1a7.jpeg', '422e6a71c792e840799e7276739ea915.jpeg', '57f9fce44bd11924a11b310f767bc031.jpeg', 'd973ab6bb6f2f2f2c6ed7b54b0121df6.jpeg', '6557c8c2e9ad58e941a7ccc12de16baa.jpeg', 'f904e10682d3e2db166a476e7a0a573f.jpeg', 'aa75a7ea802f5bcb1c17c2846c5f5b59.jpeg', '85d60e82d005a9dc9bcbda4bcded220d.jpeg', '491f90eb9e2f97fd4a7a30dd80bda5dd.jpeg', '226f669584511276b1c19e7a4da24e8d.jpeg', 'e3a64bbc6806932d723ecee9c33f4ccc.jpeg', '6785a5fcc4d82c66874f256c4bc3c0bd.jpeg', '3be2bd177b3debc4437860b78c8cf6e3.jpeg', '3020a881

In [6]:
from keras.applications.densenet import DenseNet121
from keras.applications.mobilenet import MobileNet

#model_dir = "./models/inceptionv3/"
#model_name = "inceptionv3_2018-08-25"
model_dir = "./models//vgg19/"
model_name = "vgg19——2018-08-27"
#model_dir = "./models/densenet121/"
#model_name = "DenseNet121"

"""
base_model = load_model(model_dir + model_name + '_baseline_model.h5')
model = Model(inputs=base_model.input,
                  outputs=base_model.get_layer('dense_5').output)
"""
base_model = MobileNet(include_top=True, weights=None,
                           input_tensor=None, input_shape=None,
                           pooling=None, classes=40)
base_model.load_weights("/home/anhaoran/codes/zero-shot-cnn/Baselines/zero_shot_learning_baseline/model/mobile_Animals_wgt.h5")
model = Model(inputs=base_model.input,
                  outputs=base_model.get_layer('global_average_pooling2d_1').output)
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 224, 224, 3)       0         
_________________________________________________________________
conv1_pad (ZeroPadding2D)    (None, 225, 225, 3)       0         
_________________________________________________________________
conv1 (Conv2D)               (None, 112, 112, 32)      864       
_________________________________________________________________
conv1_bn (BatchNormalization (None, 112, 112, 32)      128       
_________________________________________________________________
conv1_relu (ReLU)            (None, 112, 112, 32)      0         
_________________________________________________________________
conv_dw_1 (DepthwiseConv2D)  (None, 112, 112, 32)      288       
_________________________________________________________________
conv_dw_1_bn (BatchNormaliza (None, 112, 112, 32)      128       
__________

In [7]:
features_all = model.predict(data_x)
images_all = images_all
labels_all = labels_all
data_all = {'features_all':features_all, 
            'labels_all':labels_all,
            'images_all':images_all}
savename = "./results/" + model_name + '_features_all.pickle'
fsave = open(savename, 'wb')
pickle.dump(data_all, fsave)
fsave.close()

In [8]:
print(features_all)

[[0.         0.07333955 0.21572265 ... 0.6542377  0.         0.01238001]
 [0.         0.06389136 0.23231022 ... 0.8543207  0.0321668  0.04491273]
 [0.         0.04681206 0.34799677 ... 0.667189   0.0609375  0.07320354]
 ...
 [0.         0.0416406  0.1311415  ... 0.20613511 0.00837349 0.        ]
 [0.         0.         0.12242355 ... 0.35748497 0.         0.02458962]
 [0.         0.         0.06852442 ... 0.08675124 0.00881262 0.        ]]
